In [1]:
import sys
sys.path.append('../TorchDataPreprocessing/')
from window_slide_data import create_train_test_data

In [15]:
import torch
from torch_geometric.loader import DataLoader
import torch.nn.functional as F
from torch_geometric.nn import GCNConv, BatchNorm
import torch.nn as nn
import torch.optim as optim
from sklearn.metrics import r2_score

In [2]:
train_data_list, test_data_list = create_train_test_data()

All symbols have the same number of rows: 471
Each of the 471 dates has data for all 442 companies.
Length of DataFrame grouped by 'TargetDate': 471


d:\MANU\GNN-for-asset-management-2\GNN-for-asset-management\Models\../TorchDataPreprocessing\window_slide_data.py:121: UserWarning: Creating a tensor from a list of numpy.ndarrays is extremely slow. Please consider converting the list to a single numpy.ndarray with numpy.array() before converting to a tensor. (Triggered internally at ..\torch\csrc\utils\tensor_new.cpp:264.)
  inputs_tensor = torch.tensor(inputs, dtype=torch.float32)


In [10]:
train_data_list

[Data(x=[442, 26], edge_index=[2, 31665], y=[442], node_sectors=[442], edge_weight=[31665]),
 Data(x=[442, 26], edge_index=[2, 31665], y=[442], node_sectors=[442], edge_weight=[31665]),
 Data(x=[442, 26], edge_index=[2, 31665], y=[442], node_sectors=[442], edge_weight=[31665]),
 Data(x=[442, 26], edge_index=[2, 31665], y=[442], node_sectors=[442], edge_weight=[31665]),
 Data(x=[442, 26], edge_index=[2, 31665], y=[442], node_sectors=[442], edge_weight=[31665]),
 Data(x=[442, 26], edge_index=[2, 31665], y=[442], node_sectors=[442], edge_weight=[31665]),
 Data(x=[442, 26], edge_index=[2, 31665], y=[442], node_sectors=[442], edge_weight=[31665]),
 Data(x=[442, 26], edge_index=[2, 31665], y=[442], node_sectors=[442], edge_weight=[31665]),
 Data(x=[442, 26], edge_index=[2, 31665], y=[442], node_sectors=[442], edge_weight=[31665]),
 Data(x=[442, 26], edge_index=[2, 31665], y=[442], node_sectors=[442], edge_weight=[31665]),
 Data(x=[442, 26], edge_index=[2, 31665], y=[442], node_sectors=[442],

In [14]:
lstm_train_list = []
lstm_test_list = []

for data_obj in train_data_list:
    x = data_obj.x  # Shape might need adjusting
    y = data_obj.y  # Ensure it's in the correct shape
    lstm_train_list.append((x, y))
    
for data_obj in test_data_list:
    x = data_obj.x
    y = data_obj.y
    lstm_test_list.append((x, y))

In [17]:
from torch.utils.data import Dataset

class CustomDataset(Dataset):
    def __init__(self, data_list):
        self.data_list = data_list
    
    def __len__(self):
        return len(self.data_list)
    
    def __getitem__(self, idx):
        x, y = self.data_list[idx]
        x = x.transpose(0, 1)  # Adjusting x to be [26, 442] if needed
        y = y.unsqueeze(1)  # Adjusting y shape to [442, 1] for LSTM compatibility
        return x, y

In [28]:
# Initialize dataset and dataloader
train_dataset = CustomDataset(lstm_train_list)
test_dataset = CustomDataset(lstm_test_list)
train_loader = DataLoader(train_dataset, batch_size=1, shuffle=True)
test_loader = DataLoader(test_dataset, batch_size=1, shuffle=False)

In [29]:
for data in train_loader:
    print(data)

[tensor([[[0.0063, 0.0066, 0.0194,  ..., 0.0160, 0.0127, 0.0039],
         [0.0066, 0.0069, 0.0199,  ..., 0.0164, 0.0134, 0.0040],
         [0.0065, 0.0065, 0.0194,  ..., 0.0161, 0.0130, 0.0039],
         ...,
         [0.0065, 0.0070, 0.0226,  ..., 0.0170, 0.0124, 0.0040],
         [0.0064, 0.0070, 0.0227,  ..., 0.0170, 0.0120, 0.0039],
         [0.0066, 0.0069, 0.0227,  ..., 0.0169, 0.0123, 0.0039]]]), tensor([[[0.0067],
         [0.0068],
         [0.0250],
         [0.0050],
         [0.0076],
         [0.0070],
         [0.0142],
         [0.0136],
         [0.0095],
         [0.0070],
         [0.0122],
         [0.0096],
         [0.0052],
         [0.0070],
         [0.0016],
         [0.0043],
         [0.0081],
         [0.0093],
         [0.0069],
         [0.0132],
         [0.0093],
         [0.0101],
         [0.0100],
         [0.0094],
         [0.0030],
         [0.0011],
         [0.0003],
         [0.0087],
         [0.0219],
         [0.0180],
         [0.0133],
   

In [30]:
class LSTMModel(nn.Module):
    def __init__(self, input_dim, hidden_dim, batch_size, output_dim=1, num_layers=2):
        super(LSTMModel, self).__init__()
        self.input_dim = input_dim
        self.hidden_dim = hidden_dim
        self.batch_size = batch_size
        self.num_layers = num_layers
        
        # Define the LSTM layer
        self.lstm = nn.LSTM(self.input_dim, self.hidden_dim, self.num_layers, batch_first=True)
        
        # Define the output layer
        self.linear = nn.Linear(self.hidden_dim, output_dim)

    def forward(self, input):
        
        # Initialize hidden state with zeros
        h0 = torch.zeros(self.num_layers, input.size(0), self.hidden_dim).to(input.device)
        
        # Initialize cell state
        c0 = torch.zeros(self.num_layers, input.size(0), self.hidden_dim).to(input.device)
        
        # Forward pass through LSTM layer
        # lstm_out: tensor containing the output features `(h_t)` from the last layer of the LSTM, for each t
        # hn, cn: tensors containing the hidden state and cell state for t = seq_len
        lstm_out, (hn, cn) = self.lstm(input, (h0, c0))
        
        # Only take the output from the final timestep
        # Can pass on the entirety of lstm_out to the next layer if it is a seq2seq prediction
        out = self.linear(lstm_out[:, -1, :])
        return out

# Example instantiation of the model
input_dim = 26  # Number of input features
hidden_dim = 100  # Number of hidden neurons in LSTM layer
batch_size = 442  # Number of sequences (i.e., symbols) in each batch
num_layers = 2  # Number of LSTM layers

model = LSTMModel(input_dim, hidden_dim, batch_size, output_dim=1, num_layers=num_layers)
print(model)

LSTMModel(
  (lstm): LSTM(26, 100, num_layers=2, batch_first=True)
  (linear): Linear(in_features=100, out_features=1, bias=True)
)


In [31]:
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
model.to(device)

# Define loss function and optimizer
lr_rate = 0.001
criterion = nn.MSELoss()
optimizer = optim.Adam(model.parameters(), lr=lr_rate)

In [32]:
train_loader = DataLoader(train_data_list, batch_size=1, shuffle=True)
test_loader = DataLoader(test_data_list, batch_size=1, shuffle=False)

In [36]:
def train(model, train_loader, criterion, optimizer, device):
    model.train()
    total_loss = 0
    for data in train_loader:
        inputs, targets = data.x.to(device), data.y.to(device)
        print(f'Input shape: {inputs.shape}')  # Should print: torch.Size([batch_size, seq_len, features])
        print(f'Target shape: {targets.shape}')
        optimizer.zero_grad()
        outputs = model(inputs)
        loss = criterion(outputs, targets)
        total_loss += loss.item()
        loss.backward()
        optimizer.step()

    average_loss = total_loss / len(train_loader)
    return average_loss


In [37]:
def test(model, test_loader, criterion, device):
    model.eval()
    total_loss = 0
    all_targets = []
    all_outputs = []
    with torch.no_grad():
        for data in test_loader:
            inputs, targets = data.x.to(device), data.y.to(device)

            outputs = model(inputs)
            
            loss = criterion(outputs, targets)
            total_loss += loss.item()

            all_targets.extend(targets.view(-1).tolist())
            all_outputs.extend(outputs.view(-1).tolist())

    average_loss = total_loss / len(test_loader)
    r2 = r2_score(all_targets, all_outputs)
    return average_loss, r2

In [38]:
num_epochs = 1

for i in range(num_epochs):
    train_loss = train(model, train_loader, criterion, optimizer, device)
    test_loss, r2 = test(model, test_loader, criterion, device)
    print(f'Epoch: {i+1} -> Train Loss: {train_loss}, Test Loss: {test_loss}, R2: {r2}')

Input shape: torch.Size([442, 26])
Target shape: torch.Size([442])


RuntimeError: For unbatched 2-D input, hx and cx should also be 2-D but got (3-D, 3-D) tensors